In [38]:
import bokeh.plotting as bk
from bokeh.models import ColumnDataSource, CustomJS
from bokeh.application.handlers import FunctionHandler
from bokeh.application import Application

import numpy as np

bk.output_notebook()

Loading BokehJS ...

In [45]:
class TestPlot():
    
    def __init__(self):
        
        self.x_range = np.arange(100)
        self.y_range = np.arange(100)
        self.width = 100
        self.height = 100
        
        self.dims = ColumnDataSource(data=dict(width=[self.width], 
                                               height=[self.height], 
                                               xmin=[self.x_range.min()], 
                                               xmax=[self.x_range.max()], 
                                               ymin=[self.y_range.max()], 
                                               ymax=[self.y_range.min()]))
        
        self.dims_jscode = """
            var update_dims = function () {
                var new_data = {
                    height: [plot.plot_height],
                    width: [plot.plot_width],
                    xmin: [plot.x_range.start],
                    ymin: [plot.y_range.start],
                    xmax: [plot.x_range.end],
                    ymax: [plot.y_range.end]
                };
                dims.data = new_data;
            };
            if (typeof throttle != 'undefined' && throttle != null) {
                clearTimeout(throttle);
            }
            throttle = setTimeout(update_dims, 100, "replace");
            """
        self.dims.on_change('data', self.on_dims_change)
        self.figure = bk.figure(x_range = (self.x_range.min(),
                                           self.x_range.max()), 
                                y_range = (self.y_range.max(),
                                           self.y_range.min()))
        self.figure.x_range.callback = CustomJS(code=self.dims_jscode, 
                                                args=dict(plot=self.figure, 
                                                          dims=self.dims))
        self.figure.y_range.callback = CustomJS(code=self.dims_jscode, 
                                                args=dict(plot=self.figure, 
                                                          dims=self.dims))
        self.figure.line(np.arange(100), 0.5*np.arange(100))
        
    def on_dims_change(self, attr, old, new):
        print(self.dims.data)

    def modify_doc(self, doc):
        doc.add_root(self.figure)

In [49]:
bk.curdoc().clear()
p = TestPlot()
handler = FunctionHandler(p.modify_doc)
app = Application(handler)
bk.show(app)

In [48]:
p.dims.data

{'width': [100],
 'height': [100],
 'xmin': [0],
 'xmax': [99],
 'ymin': [99],
 'ymax': [0]}